# Land cover classification at the Mississppi Delta

In this notebook, you will use a k-means **unsupervised** clustering
algorithm to group pixels by similar spectral signatures. **k-means** is
an **exploratory** method for finding patterns in data. Because it is
unsupervised, you don’t need any training data for the model. You also
can’t measure how well it “performs” because the clusters will not
correspond to any particular land cover class. However, we expect at
least some of the clusters to be identifiable as different types of land
cover.

You will use the [harmonized Sentinel/Landsat multispectral
dataset](https://lpdaac.usgs.gov/documents/1698/HLS_User_Guide_V2.pdf).
You can access the data with an [Earthdata
account](https://www.earthdata.nasa.gov/learn/get-started) and the
[`earthaccess` library from
NSIDC](https://github.com/nsidc/earthaccess):

## STEP 1: Set up

### Step 1a: Load libraries and set GDAL parameters

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>Import all libraries you will need for this analysis</li>
<li>Configure GDAL parameters to help avoid connection errors:
<code>python      os.environ["GDAL_HTTP_MAX_RETRY"] = "5"      os.environ["GDAL_HTTP_RETRY_DELAY"] = "1"</code></li>
</ol></div></div>

In [55]:
import os       # file paths
import pickle   # for saving/loading data
import re       # regular expressions
import warnings # for ignoring warnings


import cartopy.crs as ccrs  # plotting maps
import earthaccess          # accessing Earth data API
import earthpy as et        # working with spatial data
import geopandas as gpd     # working with geospatial data
import geoviews as gv       # interactive geospatial visualizations
import holoviews as hv      # interactive plotting
import hvplot.pandas        # plotting with pandas dataframes
import hvplot.xarray        # plotting with xarray datasets
import pyogrio              # working with geospatial vector data   

import numpy as np          # working with arrays
import pandas as pd         # working with dataframes
import rioxarray as rxr     # working with geospatial raster data
import rioxarray.merge as rxrmerge  # merging geospatial raster data
from tqdm.notebook import tqdm      # progress bars
from ipywidgets import IntProgress  # progress bars
from IPython.display import display     # displaying widgets
import xarray as xr                 # working with multi-dimensional arrays
from shapely.geometry import Polygon    # working with geometric shapes
from sklearn.cluster import KMeans      # for clustering data

### set GDAL parameters
os.environ["GDAL_HTTP_MAX_RETRY"] = "5"
os.environ["GDAL_HTTP_RETRY_DELAY"] = "1"

### skip non-critical warnings
warnings.simplefilter('ignore')

### Step 1b: Run the caching decorator

Below you can find code for a caching **decorator** which you can use in
your code. To use the decorator:

``` python
@cached(key, override)
def do_something(*args, **kwargs):
    ...
    return item_to_cache
```

This decorator will **pickle** the results of running the
`do_something()` function, and only run the code if the results don’t
already exist. To override the caching, for example temporarily after
making changes to your code, set `override=True`. Note that to use the
caching decorator, you must write your own function to perform each
task!

You might notice that typically in these assignments, we start by creating a data_dir to store our data files. Here, our caching decorator is making the data directory for us.

In [2]:
# modify cache directory for my file paths
cache_dir = os.path.join(
    et.io.HOME,
    "Data",
    "Earth Analytics",
    "land-cover-clustering"
)

In [3]:
### make the caching decorator
def cached(func_key, override=False):
    """
    A decorator to cache function results
    
    Parameters
    ==========
    key: str
      File basename used to save pickled results
    override: bool
      When True, re-compute even if the results are already stored
    """
    def compute_and_cache_decorator(compute_function):
        """
        Wrap the caching function
        
        Parameters
        ==========
        compute_function: function
          The function to run and cache results
        """
        def compute_and_cache(*args, **kwargs):
            """
            Perform a computation and cache, or load cached result.
            
            Parameters
            ==========
            args
              Positional arguments for the compute function
            kwargs
              Keyword arguments for the compute function
            """
            ### Add an identifier from the particular function call
            if 'cache_key' in kwargs:
                key = '_'.join((func_key, kwargs['cache_key']))
            else:
                key = func_key

            ### define a file path based on the directory structure in earthpy
            path = os.path.join(
                
                ## established dir
                cache_dir,
                
                ### make a subdirectory called "jars"
                'jars', 
                
                ### use f-string (formatted string) to create a string by embedding the value
                ### of the variable "key" into the string 
                ### use .pickle file extension (a pickle file is a serialized python objecT)
                f'{key}.pickle')
            
            ### Check if the cache exists already or if we should override caching
            if not os.path.exists(path) or override:
                
                ### Make jars directory if needed
                os.makedirs(os.path.dirname(path), exist_ok=True)
                
                ### Run the compute function as the user did
                result = compute_function(*args, **kwargs)
                
                ### Pickle the object (save to file)
                ### open the file at filename
                with open(path, 'wb') as file:
                    
                    ### save the result without needing to recompute when loading
                    ### it back into Python
                    pickle.dump(result, file)
            
            ### if the file already exists/we are not overriding the cache
            else:
               
                ### Unpickle the object (load the cached result)
                with open(path, 'rb') as file:
                    
                    ### use pickle.load to un-serialize the file back into a python object
                    result = pickle.load(file)
                    
            return result
        
        return compute_and_cache
    
    return compute_and_cache_decorator

## STEP 2: Study site

For this analysis, you will use a watershed from the [Water Boundary
Dataset](https://www.usgs.gov/national-hydrography/access-national-hydrography-products),
HU12 watersheds (WBDHU12.shp).

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>Download the Water Boundary Dataset for region 8 (Mississippi)</li>
<li>Select watershed 080902030506</li>
<li>Generate a site map of the watershed</li>
</ol>
<p>Try to use the <strong>caching decorator</strong></p></div></div>

We chose this watershed because it covers parts of New Orleans an is
near the Mississippi Delta. Deltas are boundary areas between the land
and the ocean, and as a result tend to contain a rich variety of
different land cover and land use types.

In [4]:
### assign the hydrologic unit code
HUC_LEVEL = 12

# download, unzip, and read zip file
@cached(f'wpd_08_hu{HUC_LEVEL}_gdf')

# make a function to read in the data
def read_wpd(wpd_filename, cache_key):
    """Read in the Watershed Boundary Dataset (WBD) geospatial data"""

    # set url for the WBD data
    wpd_url = (
        
        # define url
        "https://prd-tnm.s3.amazonaws.com/StagedProducts/Hydrography/WBD/HU2/Shape/"

        # insert name of specific file name into the url
        f"{wpd_filename}.zip"
    )

    # download data and unzip
    wpd_dir = et.data.get_data(url = wpd_url)

    # path to the shapefile in dir
    wpd_path = os.path.join(wpd_dir,
                            'Shape',
                            f'WBDHU{HUC_LEVEL}.shp')
    
    # read in the shapefile as a geodataframe
    wpd_gdf = gpd.read_file(wpd_path,
                            
                            # use pyogrio library
                            # (better performance with large data)
                            engine='pyogrio')
    
    # return the geodataframe
    return wpd_gdf

In [5]:
### open the shapefile using the read_wbd_file function that we created

wpd_gdf = read_wpd("WBD_08_HU2_Shape", 
                   f'hu{HUC_LEVEL}')

In [6]:
wpd_gdf

tnmid  \
0     {8AFB1AF9-7296-4303-89DE-14CD073B859A}   
1     {916A17A6-B4A0-4FD7-9BB8-FFD1936B15B2}   
2     {493C7EC1-2F1C-4B84-AFFB-6F6868A9868E}   
3     {49A3C087-B460-4F97-9D99-78CBB675248B}   
4     {0FB41498-11EA-4AB1-AF05-E2A8E5E2E274}   
...                                      ...   
2636  {9E524E78-2605-48CB-A41F-618AFCDF513D}   
2637  {C11913D9-C534-4755-884C-4CAD470ED143}   
2638  {3EEBF422-01AC-4322-A63C-24C0A34E1E4F}   
2639  {4734715C-0F4A-4211-BBAE-86605B20B79A}   
2640  {D3C1C8A9-C189-4E05-8E90-D093F28BB762}   

                                  metasource  \
0     {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
1     {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
2     {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
3     {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
4     {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
...                                      ...   
2636  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
2637  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
2638  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
2639  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
2640  {6A1A2621-3915-4BDD-BF49-57D80A2FF16C}   

                            sourcedata  \
0     Watershed Boundary Dataset (WBD)   
1     Watershed Boundary Dataset (WBD)   
2     Watershed Boundary Dataset (WBD)   
3     Watershed Boundary Dataset (WBD)   
4     Watershed Boundary Dataset (WBD)   
...                                ...   
2636  Watershed Boundary Dataset (WBD)   
2637  Watershed Boundary Dataset (WBD)   
2638  Watershed Boundary Dataset (WBD)   
2639  Watershed Boundary Dataset (WBD)   
2640  Watershed Boundary Dataset (WBD)   

                                             sourceorig sourcefeat   loaddate  \
0     Natural Resources and Conservation Service and...       None 2024-08-15   
1     Natural Resources and Conservation Service and...       None 2024-08-15   
2     Natural Resources and Conservation Service and...       None 2024-08-15   
3     Natural Resources and Conservation Service and...       None 2024-08-15   
4     Natural Resources and Conservation Service and...       None 2024-08-15   
...                                                 ...        ...        ...   
2636  Natural Resources and Conservation Service and...       None 2024-08-15   
2637  Natural Resources and Conservation Service and...       None 2024-08-15   
2638  Natural Resources and Conservation Service and...       None 2024-08-15   
2639  Natural Resources and Conservation Service and...       None 2024-08-15   
2640  Natural Resources and Conservation Service and...       None 2024-09-30   

           referenceg  areaacres  areasqkm states  ...  \
0       535297,540579   29441.81    119.15     LA  ...   
1              535512   11406.67     46.16     LA  ...   
2       547190,559640   29138.21    117.92     LA  ...   
3         77417,78285   17759.39     71.87     AR  ...   
4             1628466   98564.62    398.88     LA  ...   
...               ...        ...       ...    ...  ...   
2636    695171,692611    9132.46     36.96     MS  ...   
2637      77280,81842   20587.50     83.31     AR  ...   
2638           714675   21405.46     86.62     MO  ...   
2639    547104,553857   38848.09    157.21     LA  ...   
2640  1627973,1628339   29780.18    120.52     LA  ...   

                                             name hutype        humod  \
0                        Gourd Bayou-Youngs Bayou      S     LE,ID,DD   
1                                      Hams Creek      S           ID   
2                     Caney Creek-Bayou D'Arbonne      S           NM   
3                      L'Aigle Creek-Saline River      S           NM   
4                           West Cote Blanche Bay      W           NM   
...                                           ...    ...          ...   
2636              Widow Bayou-Big Sunflower River      S     AW,LE,TF   
2637                Lindermans Lake-Bayou Des Arc      S           LE   
2638                                  Brewer Lake    

In [7]:
### filter the shapefile to the specific watershed we're using

### define the gdf for the watershed by sub-setting the gdf of the whole watershed dataset
delta_gdf = wpd_gdf[wpd_gdf[

    ### filter the gdf to the row(s) with the watershed we want
    ### use "dissolve" to merge the geometries of all the rows matching the target watershed

    f'huc{HUC_LEVEL}'].isin(['080902030506'])].dissolve()

### check it out
delta_gdf


geometry  \
0  POLYGON ((-89.97047 29.74687, -89.96593 29.750...   

                                    tnmid  \
0  {E942B72E-599E-48F5-908A-EA5265701C14}   

                               metasource                        sourcedata  \
0  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}  Watershed Boundary Dataset (WBD)   

                                          sourceorig sourcefeat   loaddate  \
0  Natural Resources and Conservation Service and...       None 2024-08-15   

      referenceg  areaacres  areasqkm  ...         huc12  \
0  536881,539539   37355.86    151.17  ...  080902030506   

                        name hutype humod         tohuc noncontrib  \
0  Manuel Canal-Spanish Lake      D    GC  080902030508        0.0   

   noncontr_1  shape_Leng  shape_Area  ObjectID  
0         0.0         NaN         NaN      2560  

[1 rows x 21 columns]

In [8]:
### Make a site map with satellite imagery in the background
(
    # project delta_gdf to mercator
    delta_gdf.to_crs(ccrs.Mercator())

    # use hvplot
    .hvplot(

        alpha = .2, fill_color = 'white',

        # add basemap
        tiles = 'EsriImagery',

        # plot in Mercator
        crs = ccrs.Mercator()

    # set options    
    ).opts(width = 600, height = 400)
)


:Overlay
   .WMTS.I     :WMTS   [Longitude,Latitude]
   .Polygons.I :Polygons   [Longitude,Latitude]

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-response"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div></div><div class="callout-body-container callout-body"><p>Write a 2-3 sentence <strong>site description</strong> (with
citations) of this area that helps to put your analysis in context.</p></div></div>


The specific location above, known as Manuel Canal-Spanish Lake, is part of the 'Bayou Gentilly-Bayou Terre aux Boeufs' in the Eastern Louisiana Coastal Huc 8 region in Louisiana. The eastern side of the area in question is squeezed by Lake Lery on the north and Grand Lake on the south, and most of the region appears to be wetlands or similar. The south eastern edge of New Orleans is visible in the top left of the plot and the Mississippi River runs along the western edge (). Zooming out on the plot helps locate the subject area and see the scale of the Mississippi River Delta.

Sea level rise, erosion, and lack of sediment replacement are constant threats contributing to land loss, and a number of private and public efforts are being made to mitigate the losses: [National Fish and Wildlife Foundation](https://resiliencedata.nfwf.org/dataset/b8e807bf-518b-4ab8-990a-aabacfcfb5b2/resource/8f24f832-26b8-48d4-a011-b86e0b253524/download/btab-monitoring-plan-final-11-15-22.pdf), [Royal](https://royal.us/projects/bayou-terre-aux-boeufs-ridge-restoration-armoring/) 

## STEP 3: Multispectral data

### Step 3a: Search for data

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>Log in to the <code>earthaccess</code> service using your Earthdata
credentials:
<code>python      earthaccess.login(persist=True)</code></li>
<li>Modify the following sample code to search for granules of the
HLSL30 product overlapping the watershed boundary from May to October
2023 (there should be 76 granules):
<code>python      results = earthaccess.search_data(          short_name="...",          cloud_hosted=True,          bounding_box=tuple(gdf.total_bounds),          temporal=("...", "..."),      )</code></li>
</ol></div></div>

In [9]:
### Log in to earthaccess
earthaccess.login(persist = True)

In [10]:
### Search for HLS granules we want
results = earthaccess.search_data(

    ### specify which dataset and spatial resolution we want 
    short_name = 'HLSL30',

    ### specify that we're using cloud data
    cloud_hosted = True,

    ### use the bounding box from our watershed boundary
    bounding_box = tuple(delta_gdf.total_bounds),

    ### set the temporal range of the data
    temporal = ('2024-06', '2024-08')
)

In [11]:
results

[Collection: {'EntryTitle': 'HLS Landsat Operational Land Imager Surface Reflectance and TOA Brightness Daily Global 30m v2.0'}
 Spatial coverage: {'HorizontalSpatialDomain': {'Geometry': {'GPolygons': [{'Boundary': {'Points': [{'Longitude': -89.79864173, 'Latitude': 29.70347853}, {'Longitude': -89.76643746, 'Latitude': 30.69278312}, {'Longitude': -90.91181412, 'Latitude': 30.71627038}, {'Longitude': -90.93262544, 'Latitude': 29.72659663}, {'Longitude': -89.79864173, 'Latitude': 29.70347853}]}}]}}}
 Temporal coverage: {'RangeDateTime': {'BeginningDateTime': '2024-06-07T16:31:11.509Z', 'EndingDateTime': '2024-06-07T16:31:11.509Z'}}
 Size(MB): 169.50417041778564
 Data: ['https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.B10.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.SAA.tif', 'https://data.l

### Step 3b: Compile information about each granule

I recommend building a GeoDataFrame, as this will allow you to plot the
granules you are downloading and make sure they line up with your
shapefile. You could also use a DataFrame, dictionary, or a custom
object to store this information.

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>For each search result:
<ol type="1">
<li>Get the following information (HINT: look at the [‘umm’] values for
each search result):
<ul>
<li>granule id (UR)</li>
<li>datetime</li>
<li>geometry (HINT: check out the shapely.geometry.Polygon class to
convert points to a Polygon)</li>
</ul></li>
<li>Open the granule files. I recommend opening one granule at a time,
e.g. with (<code>earthaccess.open([result]</code>).</li>
<li>For each file (band), get the following information:
<ul>
<li>file handler returned from <code>earthaccess.open()</code></li>
<li>tile id</li>
<li>band number</li>
</ul></li>
</ol></li>
<li>Compile all the information you collected into a GeoDataFrame</li>
</ol></div></div>

In [12]:
### make a function to process all the granules from the earthaccess search
### and extract information for each granule

### define the function
def get_earthaccess_links(results):

    ### make and display a progress bar
    progress_bar = IntProgress(min=0, max = len(results), description='Open granules:')
    display(progress_bar)

    ### use a regular expression to extract tile_id and bank from .tif files
    url_re = re.compile(
        r'\.(?P<tile_id>\w+)\.\d+T\d+\.v\d\.\d\.(?P<band>[A-Za-z0-9]+)\.tif')

    ### accumulate gdf rows from each granule
    link_rows = []    

    ### loop over granules to extract info
    for granule in results:

        ### locate metadata (UMM = universal metadata model)
        info_dict = granule['umm']

        ### pull out unique identifier for the granule
        granule_id = info_dict['GranuleUR']

        ### extract date/time 
        datetime = pd.to_datetime(
            info_dict['TemporalExtent']['RangeDateTime']['BeginningDateTime']
        )

        ### extract boundary coordinates for granule
        points = (
            info_dict
            ['SpatialExtent']['HorizontalSpatialDomain']['Geometry']['GPolygons'][0]
            ['Boundary']['Points']
        )

        ### make polygon using coordinate points for granule
        geometry = Polygon(
            [(point['Longitude'], 
              point['Latitude']) for point in points]
        )

        ### get url and open granule
        files = earthaccess.open([granule])

        ### loop through each file in the granule
        for file in files:

            ### use url regular expression to get url
            match = url_re.search(file.full_name)

            ### if match is found, append data to link_rows gdf we initialized
            if match is not None:
                link_rows.append(

                    ### makes a gdf with the granule's data and geometry
                    gpd.GeoDataFrame(
                        dict(

                            # timestamp
                            datetime = [datetime],
                           
                            # unique tile ID
                            tile_id = [match.group('tile_id')], 

                            # band 
                            band = [match.group('band')],

                            # url
                            url = [file],

                            # polygon
                            geometry = [geometry]
                        ),

                        crs = 'EPSG:4326'
                    
                    )
                )
        ### update progress bar after each granule is done
        progress_bar.value += 1

    ### combine into a single gdf   
    file_df = pd.concat(link_rows).reset_index(drop = True)

    ### return the final gdf file
    return file_df

In [13]:
# look at one granule
test_granule = results[0]

test_granule

Collection: {'EntryTitle': 'HLS Landsat Operational Land Imager Surface Reflectance and TOA Brightness Daily Global 30m v2.0'}
Spatial coverage: {'HorizontalSpatialDomain': {'Geometry': {'GPolygons': [{'Boundary': {'Points': [{'Longitude': -89.79864173, 'Latitude': 29.70347853}, {'Longitude': -89.76643746, 'Latitude': 30.69278312}, {'Longitude': -90.91181412, 'Latitude': 30.71627038}, {'Longitude': -90.93262544, 'Latitude': 29.72659663}, {'Longitude': -89.79864173, 'Latitude': 29.70347853}]}}]}}}
Temporal coverage: {'RangeDateTime': {'BeginningDateTime': '2024-06-07T16:31:11.509Z', 'EndingDateTime': '2024-06-07T16:31:11.509Z'}}
Size(MB): 169.50417041778564
Data: ['https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.B10.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.SAA.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.VZA.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.B06.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.B09.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.B04.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.B03.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.B07.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.VAA.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.Fmask.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.B01.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.SZA.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.B11.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.B05.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T15RYP.2024159T163111.v2.0/HLS.L30.T15RYP.2024159T163111.v2.0.B02.tif']

In [14]:
# look at umm
info_dict = test_granule['umm']
info_dict

{'TemporalExtent': {'RangeDateTime': {'BeginningDateTime': '2024-06-07T16:31:11.509Z',
   'EndingDateTime': '2024-06-07T16:31:11.509Z'}},
 'GranuleUR': 'HLS.L30.T15RYP.2024159T163111.v2.0',
 'AdditionalAttributes': [{'Name': 'LANDSAT_PRODUCT_ID',
   'Values': ['LC08_L1TP_022039_20240607_20240607_02_RT']},
  {'Name': 'CLOUD_COVERAGE', 'Values': ['10']},
  {'Name': 'MGRS_TILE_ID', 'Values': ['15RYP']},
  {'Name': 'SPATIAL_COVERAGE', 'Values': ['100']},
  {'Name': 'SPATIAL_RESOLUTION', 'Values': ['30.0']},
  {'Name': 'SPATIAL_RESAMPLING_ALG', 'Values': ['Cubic Convolution']},
  {'Name': 'HLS_PROCESSING_TIME', 'Values': ['2024-06-21T18:26:46Z']},
  {'Name': 'SENSING_TIME', 'Values': ['2024-06-07T16:31:11.5093050Z']},
  {'Name': 'HORIZONTAL_CS_NAME', 'Values': ['UTM, WGS84, UTM ZONE 15']},
  {'Name': 'ULX', 'Values': ['699960.0']},
  {'Name': 'ULY', 'Values': ['3400020.0']},
  {'Name': 'ADD_OFFSET', 'Values': ['0']},
  {'Name': 'REF_SCALE_FACTOR', 'Values': ['0.0001']},
  {'Name': 'THERM_SC

In [15]:
# run the function to get granule search results

# set path to save file
links_path = os.path.join(
    cache_dir,
    "downloads",
    'links_file_df.gpkg'
)

if os.path.exists(links_path):
    links_file_df = gpd.read_file(links_path)
else:    
    links_file_df = get_earthaccess_links(results)
    os.makedirs(os.path.dirname(links_path), exist_ok=True)
    links_file_df.to_file(links_path, driver = "GPKG")

In [16]:
links_file_df

datetime tile_id   band  \
0   2024-06-07 16:31:11.509000+00:00  T15RYP    B10   
1   2024-06-07 16:31:11.509000+00:00  T15RYP    SAA   
2   2024-06-07 16:31:11.509000+00:00  T15RYP    VZA   
3   2024-06-07 16:31:11.509000+00:00  T15RYP    B06   
4   2024-06-07 16:31:11.509000+00:00  T15RYP    B09   
..                               ...     ...    ...   
655 2024-08-26 16:31:51.172000+00:00  T15RYN    SAA   
656 2024-08-26 16:31:51.172000+00:00  T15RYN    B11   
657 2024-08-26 16:31:51.172000+00:00  T15RYN    SZA   
658 2024-08-26 16:31:51.172000+00:00  T15RYN  Fmask   
659 2024-08-26 16:31:51.172000+00:00  T15RYN    B06   

                                                   url  \
0    <File-like object HTTPFileSystem, https://data...   
1    <File-like object HTTPFileSystem, https://data...   
2    <File-like object HTTPFileSystem, https://data...   
3    <File-like object HTTPFileSystem, https://data...   
4    <File-like object HTTPFileSystem, https://data...   
..                                                 ...   
655  <File-like object HTTPFileSystem, https://data...   
656  <File-like object HTTPFileSystem, https://data...   
657  <File-like object HTTPFileSystem, https://data...   
658  <File-like object HTTPFileSystem, https://data...   
659  <File-like object HTTPFileSystem, https://data...   

                                              geometry  
0    POLYGON ((-89.79864 29.70348, -89.76644 30.692...  
1    POLYGON ((-89.79864 29.70348, -89.76644 30.692...  
2    POLYGON ((-89.79864 29.70348, -89.76644 30.692...  
3    POLYGON ((-89.79864 29.70348, -89.76644 30.692...  
4    POLYGON ((-89.79864 29.70348, -89.76644 30.692...  
..                                                 ...  
655  POLYGON ((-89.82661 28.80214, -89.79584 29.791...  
656  POLYGON ((-89.82661 28.80214, -89.79584 29.791...  
657  POLYGON ((-89.82661 28.80214, -89.79584 29.791...  
658  POLYGON ((-89.82661 28.80214, -89.79584 29.791...  
659  POLYGON ((-89.82661 28.80214, -89.79584 29.791...  

[660 rows x 5 columns]

### Step 3c: Open, crop, and mask data

This will be the most resource-intensive step. I recommend caching your
results using the `cached` decorator or by writing your own caching
code. I also recommend testing this step with one or two dates before
running the full computation.

This code should include at least one **function** including a
numpy-style docstring. A good place to start would be a function for
opening a single masked raster, applying the appropriate scale
parameter, and cropping.

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>For each granule:
<ol type="1">
<li><p>Open the Fmask band, crop, and compute a quality mask for the
granule. You can use the following code as a starting point, making sure
that <code>mask_bits</code> contains the quality bits you want to
consider: ```python # Expand into a new dimension of binary bits bits =
( np.unpackbits(da.astype(np.uint8), bitorder=‘little’)
.reshape(da.shape + (-1,)) )</p>
<p># Select the required bits and check if any are flagged mask =
np.prod(bits[…, mask_bits]==0, axis=-1) ```</p></li>
<li><p>For each band that starts with ‘B’:</p>
<ol type="1">
<li>Open the band, crop, and apply the scale factor</li>
<li>Name the DataArray after the band using the <code>.name</code>
attribute</li>
<li>Apply the cloud mask using the <code>.where()</code> method</li>
<li>Store the DataArray in your data structure (e.g. adding a
GeoDataFrame column with the DataArray in it. Note that you will need to
remove the rows for unused bands)</li>
</ol></li>
</ol></li>
</ol></div></div>

In [17]:
### apply cached decorator to function
@cached('delta_reflectance_da_df')


### write function that computes reflectance data using 
### search results (df of urls) and watershed boundary
def compute_reflectance_da(search_results, boundary_gdf):

    """
    Connect to files using VSI, crop the, apply a cloud mask, and wrangle the data.

    Return a single reflectance DF with bands as columns and centroid coords & datetime as index

    Parameters
    ==========
    search_results_list: list
        Search result links to the files (urls)
    boundary_gdf: gpd.GeoDataFrame
        Boundary used to crop the data
    """

    ### write a function to open raster from url, apply scale factor, crop, and mask data
    def open_dataaray(url, boundary_proj_gdf, scale = 1, masked = True):

        # open raster data
        da = rxr.open_rasterio(url, masked = masked).squeeze() * scale

        # reproject boundary if needed to match raster crs
        if boundary_proj_gdf is None:
            boundary_proj_gdf = boundary_gdf.to_crs(da.rio.crs)

        # crop raster to bounding box
        cropped = da.rio.clip_box(*boundary_proj_gdf.total_bounds)

        return cropped
        
    ### write function to apply a cloud mask
    def compute_quality_mask(da, mask_bits = [1, 2, 3]):

        """Mask out low quality data by bit"""

        # unpack the bits to a new axis
        bits = (

            # unpack each number into individual bits
            np.unpackbits(

                # convert to 8-bit unsigned int format
                da.astype(np.uint8),

                # set order of bits
                bitorder = 'little'

            # reshape to match original data with extra dim for bits
            ).reshape(da.shape + (-1,))
        )

        # select desired bits
        selected_bits = bits[..., mask_bits]

        # check they are all zero
        mask = np.all(selected_bits == 0, axis=-1)


        ### return the mask
        return mask
    

    ### grab metadata
    file_df = get_earthaccess_links(search_results)

    # store results for each granule
    granule_da_rows = []    

    # store projected boundary
    boundary_proj_gdf = None
    
    # group the data by granule
    group_iter = file_df.groupby(

        # datetime and tile_id
        ['datetime', 'tile_id']
    )

    ## loop through each image and its metadata
    for (datetime, tile_id), granule_df in tqdm(group_iter):

        # print status bar
        print(f'Processing granule {tile_id} {datetime}')

        # find each granule's cloud mask file (fmask) url
        cloud_mask_url = (
            granule_df.loc[granule_df.band == 'Fmask', 'url']
            .values[0])

        # open granule cloud mask
        cloud_masked_cropped_da = open_dataaray(cloud_mask_url, boundary_proj_gdf, masked = False)

        ### compute cloud mask
        cloud_mask = compute_quality_mask(cloud_masked_cropped_da)

        ### loop through each spectral band to open, crop, and mask the band
        da_list = []
        df_list = []

        # loop through each band in granule
        for i, row in granule_df.iterrows():

            # only loop through spectral bands
            if row.band.startswith('B'):

                # open band's raster and scale to reflectance data
                band_cropped = open_dataaray(
                    row.url, boundary_proj_gdf, scale = .0001)

                # name the raster by the band
                band_cropped.name = row.band    

                # apply the cloud mask to the raster
                row['da'] = band_cropped.where(cloud_mask)
                
                ### append the row to granule_da_rows
                granule_da_rows.append(row.to_frame().T)

    ### reassemble the metadata df
    return pd.concat(granule_da_rows)


In [18]:
# apply the function

reflectance_da_df = compute_reflectance_da(results, delta_gdf)

IntProgress(value=0, description='Open granules:', max=44)

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/15 [00:00<?, ?it/s]

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

...

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/15 [00:00<?, ?it/s]

  0%|          | 0/44 [00:00<?, ?it/s]

Processing granule T15RYN 2024-06-07 16:31:11.509000+00:00
Processing granule T15RYP 2024-06-07 16:31:11.509000+00:00
Processing granule T16RBT 2024-06-07 16:31:11.509000+00:00
Processing granule T16RBU 2024-06-07 16:31:11.509000+00:00
Processing granule T15RYN 2024-06-15 16:31:19.154000+00:00
Processing granule T15RYP 2024-06-15 16:31:19.154000+00:00
Processing granule T16RBT 2024-06-15 16:31:19.154000+00:00
Processing granule T16RBU 2024-06-15 16:31:19.154000+00:00
Processing granule T15RYN 2024-06-23 16:31:21.277000+00:00
Processing granule T15RYP 2024-06-23 16:31:21.277000+00:00
Processing granule T16RBT 2024-06-23 16:31:21.277000+00:00
Processing granule T16RBU 2024-06-23 16:31:21.277000+00:00
Processing granule T15RYN 2024-07-01 16:31:17.338000+00:00
Processing granule T15RYP 2024-07-01 16:31:17.338000+00:00
Processing granule T16RBT 2024-07-01 16:31:17.338000+00:00
Processing granule T16RBU 2024-07-01 16:31:17.338000+00:00
Processing granule T15RYN 2024-07-09 16:31:29.187000+00:

In [ ]:
# test the function

reflectance_da_df.head()

### Step 3d: Merge and Composite Data

You will notice for this watershed that:   
1. The raster data for each date are spread across 4 granules  
2. Any given image is incomplete because of clouds

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">

*   1. For each band:  
    *   a. For each date:  
        *   i. Merge all 4 granules  
        *   ii. Mask any negative values created by interpolating from the nodata value of -9999 (`rioxarray`) should account for this, but doesn't appear to when merging. If you leave these values in, they will create problems later on
    *   b. Concatenate the merged DataArrays along a new date dimension  
    *   c. Take the mean in the date dimension to create a composite image that fills cloud gaps  
    *   d. Add the band as a dimensions, and give the DataArray a name  
*   2. Concatenate along the band dimension


In [19]:
### apply cache decorator
@cached('delta_reflectance_da')

### create a function to merge and composite reflectance data from multiple granules
### end result: single, composite reflectance image for each spectral band
def merge_and_composite_arrays(granule_da_df):

    ### initialize a list to store composites after processing
    da_list = []    

    ### loop over each spectral band
    for band, band_df in granule_da_df.groupby('band'):

        # list for storing merged data arrays (one per date)
        merged_das = []

        ### loop over date/time of image acquisition and merge granules for each date
        for datetime, date_df in band_df.groupby('datetime'):
           
            # merge granules for each date
            merged_da = rxrmerge.merge_arrays(list(date_df.da))

            ### mask negative values (could be no data or invalid data)
            merged_da = merged_da.where(merged_da > 0)
            
            ### append to merged_das list we initialized
            merged_das.append(merged_da)
            
        ### composite images across dates
        composite_da = xr.concat(merged_das,
                                # make a datetime dim
                                # calculate median value across datetimes for pixel
                                dim = 'datetime').median('datetime')
        
        # assign band number to attribute of composite data array
        composite_da['band'] = int(band[1:])

        # name the composite data array
        composite_da.name = 'reflectance'

        ### add processed and composite data array to list
        da_list.append(composite_da)


    ### concatenates composite data arrays for each band along band dimension
    return xr.concat(da_list, dim = 'band')

In [20]:
### call function to get final composite reflectance data 

reflectance_da = merge_and_composite_arrays(reflectance_da_df)

In [21]:
# test it
reflectance_da

<xarray.DataArray 'reflectance' (band: 10, y: 556, x: 624)> Size: 14MB
array([[[nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        ...,
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan]],

       [[nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        ...,
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan]],

       [[nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        ...,
...
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan]],

       [[nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        ...,
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan]],

       [[nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        ...,
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan],
        [nan, nan, nan, ..., nan, nan, nan]]],
      shape=(10, 556, 624), dtype=float32)
Coordinates:
  * x            (x) float64 5kB 7.926e+05 7.926e+05 ... 8.112e+05 8.113e+05
  * y            (y) float64 4kB 3.304e+06 3.304e+06 ... 3.287e+06 3.287e+06
  * band         (band) int64 80B 1 2 3 4 5 6 7 9 10 11
    spatial_ref  int64 8B 0

## STEP 4: K-means clustering

Cluster your data by spectral signature using the k-means algorithm.

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>Convert your DataArray into a <strong>tidy</strong> DataFrame of
reflectance values (hint: check out the <code>.to_dataframe()</code> and
<code>.unstack()</code> methods)</li>
<li>Filter out all rows with no data (all 0s or any N/A values)</li>
<li>Fit a k-means model. You can experiment with the number of groups to
find what works best.</li>
</ol></div></div>

In [22]:
### Convert spectral DataArray to a tidy DataFrame
model_df = (reflectance_da
            
            # flatten da into long df
            .to_dataframe()

            # select reflectance column
            .reflectance

            # make the table wide: each row will be a pixel location
            # each column is a spectral band with reflectance value
            .unstack('band')
            )

### filter out rows with no data
model_df = model_df.drop(columns = [10, 11]).dropna()
model_df

band                              1       2       3       4       5       6  \
y            x                                                                
3.303783e+06 810148.062907  0.01560  0.0225  0.0409  0.0366  0.0478  0.0281   
             810178.062907  0.01895  0.0256  0.0396  0.0413  0.0426  0.0284   
             810208.062907  0.01915  0.0246  0.0387  0.0377  0.0384  0.0273   
             810238.062907  0.02040  0.0247  0.0440  0.0445  0.0629  0.0418   
             810268.062907  0.01815  0.0245  0.0437  0.0444  0.0618  0.0397   
...                             ...     ...     ...     ...     ...     ...   
3.287163e+06 793768.062907  0.02650  0.0345  0.0548  0.0427  0.0218  0.0098   
             793798.062907  0.02790  0.0351  0.0549  0.0439  0.0221  0.0104   
             793828.062907  0.02580  0.0331  0.0534  0.0419  0.0194  0.0080   
             793858.062907  0.02570  0.0326  0.0521  0.0402  0.0182  0.0064   
             793888.062907  0.02550  0.0340  0.0541  0.0423  0.0199  0.0083   

band                             7       9  
y            x                              
3.303783e+06 810148.062907  0.0181  0.0006  
             810178.062907  0.0220  0.0006  
             810208.062907  0.0236  0.0007  
             810238.062907  0.0266  0.0007  
             810268.062907  0.0259  0.0008  
...                            ...     ...  
3.287163e+06 793768.062907  0.0074  0.0007  
             793798.062907  0.0076  0.0008  
             793828.062907  0.0059  0.0009  
             793858.062907  0.0046  0.0007  
             793888.062907  0.0060  0.0007  

[317917 rows x 8 columns]

Now we're reading to fit the k-means clustering model. We can run the fit and prediction functions at the same time because we don't have target data.

In [23]:
min_values = model_df.min()
max_values = model_df.max()

print(min_values)
print(max_values)

band
1    0.0003
2    0.0021
3    0.0100
4    0.0075
5    0.0005
6    0.0006
7    0.0010
9    0.0002
dtype: float32
band
1    0.31425
2    0.35160
3    0.42865
4    0.44420
5    0.59500
6    0.49645
7    0.34510
9    0.00125
dtype: float32


In [24]:
### initialize k-means model 
k_means = KMeans(n_clusters = 5)

### fit model and predict
prediction = k_means.fit_predict(model_df.values)

### add the predicted values back to the model dataframe
model_df['cluster'] = prediction

model_df

band                              1       2       3       4       5       6  \
y            x                                                                
3.303783e+06 810148.062907  0.01560  0.0225  0.0409  0.0366  0.0478  0.0281   
             810178.062907  0.01895  0.0256  0.0396  0.0413  0.0426  0.0284   
             810208.062907  0.01915  0.0246  0.0387  0.0377  0.0384  0.0273   
             810238.062907  0.02040  0.0247  0.0440  0.0445  0.0629  0.0418   
             810268.062907  0.01815  0.0245  0.0437  0.0444  0.0618  0.0397   
...                             ...     ...     ...     ...     ...     ...   
3.287163e+06 793768.062907  0.02650  0.0345  0.0548  0.0427  0.0218  0.0098   
             793798.062907  0.02790  0.0351  0.0549  0.0439  0.0221  0.0104   
             793828.062907  0.02580  0.0331  0.0534  0.0419  0.0194  0.0080   
             793858.062907  0.02570  0.0326  0.0521  0.0402  0.0182  0.0064   
             793888.062907  0.02550  0.0340  0.0541  0.0423  0.0199  0.0083   

band                             7       9  cluster  
y            x                                       
3.303783e+06 810148.062907  0.0181  0.0006        2  
             810178.062907  0.0220  0.0006        2  
             810208.062907  0.0236  0.0007        2  
             810238.062907  0.0266  0.0007        2  
             810268.062907  0.0259  0.0008        2  
...                            ...     ...      ...  
3.287163e+06 793768.062907  0.0074  0.0007        2  
             793798.062907  0.0076  0.0008        2  
             793828.062907  0.0059  0.0009        2  
             793858.062907  0.0046  0.0007        2  
             793888.062907  0.0060  0.0007        2  

[317917 rows x 9 columns]

## STEP 5: Plot

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><p>Create a plot that shows the k-means clusters next to an RGB image of
the area. You may need to brighten your RGB image by multiplying it by
10. The code for reshaping and plotting the clusters is provided for you
below, but you will have to create the RGB plot yourself!</p>
<p>So, what is <code>.sortby(['x', 'y'])</code> doing for us? Try the
code without it and find out.</p></div></div>

In [87]:
### make data array with bands to use for rgb: red, green, and blue
rgb = reflectance_da.sel(band = [4, 3, 2])


In [ ]:
# plot rgb

# remove floating label
rgb_plot_clean = rgb_sat.reset_coords(drop=True)


rgb.hvplot.rgb(y = 'y',
                x = 'x',
                bands = 'band',
                data_aspect = 1,
                xaxis = None,
                yaxis = None,
                )

:RGB   [x,y]   (R,G,B)

In [93]:
rgb_uint8 = (rgb * 255).astype(np.uint8).where(rgb != np.nan)
rgb_uint8

<xarray.DataArray 'reflectance' (band: 3, y: 556, x: 624)> Size: 4MB
array([[[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]],

       [[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]],

       [[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]]],
      shape=(3, 556, 624), dtype=float32)
Coordinates:
  * x            (x) float64 5kB 7.926e+05 7.926e+05 ... 8.112e+05 8.113e+05
  * y            (y) float64 4kB 3.304e+06 3.304e+06 ... 3.287e+06 3.287e+06
  * band         (band) int64 24B 4 3 2
    spatial_ref  int64 8B 0

In [94]:
# plot rgb

rgb_uint8.hvplot.rgb(y = 'y',
                x = 'x',
                bands = 'band',
                data_aspect = 1,
                xaxis = None,
                yaxis = None,
                )

:RGB   [x,y]   (R,G,B)

In [95]:
rgb_uint8_bright = rgb_uint8*10

In [96]:
rgb_uint8_bright.hvplot.rgb(y = 'y',
                x = 'x',
                bands = 'band',
                data_aspect = 1,
                xaxis = None,
                yaxis = None,
                )

:RGB   [x,y]   (R,G,B)

In [97]:
# cap saturation
rgb_sat = rgb_uint8_bright.where(rgb_uint8_bright < 255, 255)

In [102]:
# plot
rgb_display = rgb_sat.reset_coords(drop=True)

rgb_display.hvplot.rgb(y = 'y',
                x = 'x',
                bands = 'band',
                data_aspect = 1,
                xaxis = None,
                yaxis = None,
                )

:RGB   [x,y]   (R,G,B)

In [103]:
# plot the kmeans clusters

(

    model_df.cluster.to_xarray().hvplot(
        x = 'x',
        y = 'y',
        data_aspect = 1,
        xaxis = None,
        yaxis = None
    )
)

:Image   [x,y]   (cluster)

In [104]:
# plot the kmeans clusters in correct order

(

    model_df.cluster.to_xarray().sortby(['x','y']).hvplot(
        x = 'x',
        y = 'y',
        data_aspect = 1,
        xaxis = None,
        yaxis = None
    )
)

:Image   [x,y]   (cluster)

In [106]:
### plot the k-means clusters next to the rgb map
(
    rgb_display.hvplot.rgb(y = 'y',
                x = 'x',
                bands = 'band',
                data_aspect = 1,
                xaxis = None,
                yaxis = None,
                )
    + 
    model_df.cluster.to_xarray().sortby(['x', 'y']).hvplot(
        cmap="Colorblind", aspect='equal') 
)

:Layout
   .RGB.I   :RGB   [x,y]   (R,G,B)
   .Image.I :Image   [x,y]   (cluster)

In [117]:
# add boundary

# Reproject boundary to match raster CRS
boundary = delta_gdf.to_crs(rgb_sat.rio.crs).hvplot(
    line_color="black",
    line_width=2,
    fill_alpha=0
)

### plot the k-means clusters with boundary added to both

(
    rgb_display.hvplot.rgb(
        y='y',
        x='x',
        bands='band',
        data_aspect=1,
        xaxis=None,
        yaxis=None,
    ) * boundary

    +

    model_df.cluster
        .to_xarray()
        .sortby(['x', 'y'])
        .hvplot(
            cmap="Colorblind",
            aspect='equal'
        ) * boundary
)


:Layout
   .Overlay.I  :Overlay
      .RGB.I      :RGB   [x,y]   (R,G,B)
      .Polygons.I :Polygons   [x,y]
   .Overlay.II :Overlay
      .Image.I    :Image   [x,y]   (cluster)
      .Polygons.I :Polygons   [x,y]

In [122]:
# fix the resizing

# Reproject boundary to raster CRS
boundary = delta_gdf.to_crs(rgb_sat.rio.crs).hvplot(
    line_color="black",
    line_width=2,
    fill_alpha=0
)

xmin, xmax = float(rgb_sat.x.min()), float(rgb_sat.x.max())
ymin, ymax = float(rgb_sat.y.min()), float(rgb_sat.y.max())

new_plot = (
    # RGB plot with boundary
    (rgb_display.hvplot.rgb(
        y='y',
        x='x',
        bands='band',
        xaxis=None,
        yaxis=None,
        frame_width=400,
        frame_height=400,
        xlim=(xmin, xmax),
        ylim=(ymin, ymax)
    ) * boundary)

    +

    # KMeans plot with boundary
    (model_df.cluster.to_xarray().sortby(['x','y']).hvplot(
        cmap="Colorblind",
        aspect='equal',
        xaxis=None,
        yaxis=None,
        frame_width=400,
        frame_height=400,
        xlim=(xmin, xmax),
        ylim=(ymin, ymax)
    ) * boundary)
).opts(
    title="KMeans Clustering of Manuel Canal-Spanish Lake, LA "
)

new_plot


:Layout
   .Overlay.I  :Overlay
      .RGB.I      :RGB   [x,y]   (R,G,B)
      .Polygons.I :Polygons   [x,y]
   .Overlay.II :Overlay
      .Image.I    :Image   [x,y]   (cluster)
      .Polygons.I :Polygons   [x,y]

In [130]:
# fixed the colorbar
from bokeh.models import FixedTicker
from bokeh.palettes import Colorblind

cluster_xr = model_df["cluster"].astype("int").to_xarray().sortby(["x", "y"]) 
kmeans_plot = (cluster_xr.hvplot(
    cmap=Colorblind[5], # 5 discrete colors 
    clim=(-0.5, 4.5), # center colors on integer classes 
    aspect='equal', 
    xaxis=None, 
    yaxis=None, 
    frame_width=400, 
    frame_height=400, 
    xlim=(xmin, xmax), 
    ylim=(ymin, ymax), 
    colorbar=True ) .
    opts( 
        colorbar_opts={ 
            "ticker": FixedTicker(ticks=[0, 1, 2, 3, 4]) # fix the colorbar intervals 
        } 
)) 
# RGB + boundary 
rgb_plot = rgb_display.hvplot.rgb(
    y='y', 
    x='x', 
    bands='band', 
    xaxis=None, 
    yaxis=None, 
    frame_width=400, 
    frame_height=400, 
    xlim=(xmin, xmax), 
    ylim=(ymin, ymax) ) * boundary 

# KMeans + boundary (with fixed colorbar) 
kmeans_plot = kmeans_plot * boundary 

#Layout side-by-side 
layout2 = (rgb_plot + kmeans_plot).opts(
    title="KMeans Clustering of Manuel Canal-Spanish Lake, LA "
)

layout2

:Layout
   .Overlay.I  :Overlay
      .RGB.I      :RGB   [x,y]   (R,G,B)
      .Polygons.I :Polygons   [x,y]
   .Overlay.II :Overlay
      .Image.I    :Image   [x,y]   (cluster)
      .Polygons.I :Polygons   [x,y]

## Clean Version

In [131]:
# import colorbar and ticker options
from bokeh.models import FixedTicker
from bokeh.palettes import Colorblind

# define scale and bounds

xmin, xmax = float(rgb_sat.x.min()), float(rgb_sat.x.max())
ymin, ymax = float(rgb_sat.y.min()), float(rgb_sat.y.max())

# set options
common_opts = dict(
    xaxis=None,
    yaxis=None,
    frame_width=400,
    frame_height=400,
    aspect="equal",
    xlim=(xmin, xmax),
    ylim=(ymin, ymax),
)

# pull in boundary
boundary = (
    delta_gdf
    .to_crs(rgb_sat.rio.crs)
    .hvplot(line_color="black", line_width=2, fill_alpha=0)
)

# pull in rgb plot (using display)
rgb_plot = (
    rgb_display.hvplot.rgb(
        y="y",
        x="x",
        bands="band",
        **common_opts
    )
    * boundary
)

# pull in k-means and define colorbar
cluster_xr = (
    model_df["cluster"]
    .astype(int)
    .to_xarray()
    .sortby(["x", "y"])
)

kmeans_plot = (
    cluster_xr.hvplot(
        cmap=Colorblind[5],
        clim=(-0.5, 4.5),
        colorbar=True,
        **common_opts
    )
    .opts(colorbar_opts={
        "ticker": FixedTicker(ticks=[0,1,2,3,4])
    })
    * boundary
)

# combine plots and title
new_plot2 = (rgb_plot + kmeans_plot).opts(
    # title still generates above the plot layout but best I have done
    title="KMeans Clustering of Manuel Canal-Spanish Lake, LA",
    shared_axes=True
)

new_plot2


:Layout
   .Overlay.I  :Overlay
      .RGB.I      :RGB   [x,y]   (R,G,B)
      .Polygons.I :Polygons   [x,y]
   .Overlay.II :Overlay
      .Image.I    :Image   [x,y]   (cluster)
      .Polygons.I :Polygons   [x,y]

In [129]:
# save
hv.save(new_plot2, "img/kmeans_output.html")

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-respond"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Reflect and Respond</div></div><div class="callout-body-container callout-body"><p>Don’t forget to interpret your plot!</p></div></div>

My plot appears to group k-means clusters by bins of similar reflectance value as expected, but is unable to differentiate between clusters without a high enough reflectance. This is also unsurprising to an extent as there is clearly greater variability in reflectance over land than water. The RGB plot is harder to interpret, but from previous analysis of the subject area, I am confident that the largest unbroken cluster is primarily over water and the other clusters differ over land features.